## Simple agent the that randomly chooses allowable actions within a silhouette ('viable' actions)

Programming this agent as a baseline.
If we can bias the agent towards e.g. bigger blocks, that's a plus.

### input
Bitmap representation of each stimulus

### output
Output block placements as dataframe of same type as action dataframe used in other analyses (dfi) i.e.
targetName, blockNum, x,y,w,h

### stability
Blocks have to be placed on a 'floor', which includes two separated floors (to make a henge) 

In the experiment, unstable placements end the trial. We could:
a) allow the agent to make unstable placements, but end the trial when they do
b) not allow the agent to consider unstable placements
Here I go for option b, where possible actions don't include those that would fall

### action selection 
There are various ways to make a random agent:
a) enumerate all possible actions (all blocks in all locations), then uniformly select from these.
b) uniformly select a block, then uniformly select a location.
c) uniformly select a location, then uniformly select a block that fits there. 
d) uniformly select a block **and** uniformly select a location, reject if not possible.



In [202]:
from __future__ import division

import numpy as np
import os, sys
from PIL import Image
from os import listdir
from os.path import isfile, join
import urllib, io
os.getcwd()
sys.path.append("..")
sys.path.append("../utils")
proj_dir = os.path.abspath('../..')

from matplotlib import pylab, mlab, pyplot
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from matplotlib.path import Path
import matplotlib.patches as patches
%matplotlib inline

from IPython.core.pylabtools import figsize, getfigs

import seaborn as sns

import random

from scipy.stats import norm
from IPython.display import clear_output

import numpy as np
import pandas as pd
import os
import json

import copy
import importlib

### Add Paths

## root paths
curr_dir = os.getcwd()
proj_dir = os.path.abspath(os.path.join(curr_dir,'..','..')) ## use relative paths

## add helpers to python path
import sys
if os.path.join(proj_dir, 'stimuli') not in sys.path:
    sys.path.append(os.path.join(proj_dir, 'stimuli'))

## custom helper modules
import separation_axis_theorem as sat
#import blockworld_helpers as utils
#import display_world as stability #may want to make a separate module for stability

def cls():
    os.system('cls' if os.name=='nt' else 'clear')

import scoring
    

In [200]:
## directory & file hierarchy
proj_dir = os.path.abspath('..')
datavol_dir = os.path.join(proj_dir,'data')
analysis_dir = os.path.abspath(os.path.join(os.getcwd(),'..'))
results_dir = os.path.join(proj_dir,'results')
plot_dir = os.path.join(results_dir,'plots')
csv_dir = os.path.join(results_dir,'csv')
json_dir = os.path.join(results_dir,'json')
exp_dir = os.path.abspath(os.path.join(proj_dir,'experiments'))
png_dir = os.path.abspath(os.path.join(datavol_dir,'png'))
jefan_dir = os.path.join(analysis_dir,'jefan')
will_dir = os.path.join(analysis_dir,'will')

## add helpers to python path
if os.path.join(proj_dir,'stimuli') not in sys.path:
    sys.path.append(os.path.join(proj_dir,'stimuli'))
    
if not os.path.exists(results_dir):
    os.makedirs(results_dir)
    
if not os.path.exists(plot_dir):
    os.makedirs(plot_dir)   
    
if not os.path.exists(csv_dir):
    os.makedirs(csv_dir)   

In [215]:
#### Target maps: grab the bitmap representation of each stim

targets = ['hand_selected_004', 'hand_selected_005', 'hand_selected_006',
       'hand_selected_008', 'hand_selected_009', 'hand_selected_011',
       'hand_selected_012', 'hand_selected_016']

target_maps = {}

with open(os.path.abspath('../results/csv/targetMaps.txt')) as json_file:
    target_maps = json.load(json_file)
    

def check_overlap(x,y,w,h,world, mode='inside'):
    overlaps = False
    
    if mode == 'inside':
        overlaps = np.all(world[x:(x+w),y:(y+h)])
    elif mode == 'outside':
        overlaps = ~np.any(world[x:(x+w),y:(y+h)])
    else:
        return
    
    return overlaps

def check_stability(x,y,w,h,world):
    '''
    checks to see if block would be supported without falling using heuristics.
    Does not allow side-supported blocks, which are sometimes possible in the real experiments
    '''
    
    if y == 0: #if on the floor then will be stable
        return True
    else: #if greater than 1/2 of the block is supported then stable
        support = world[x:(x+w),y-1:y].astype(int)
        if np.sum(support) > w/2:
            return True
        # supports on both sides of long block
        elif (w == 4 & (sum(world[x:(x+2),y-1:y].astype(int)) > 1) & (sum(world[x+2:(x+w),y-1:y].astype(int)) > 1)):
            print('4:', world[x:(x+2),y-1:y].astype(int))
            return True
        else:
              return False

def find_positions(world, block, x_offset = 5):
    
    positions = []
    
    for i in range(world.shape[0]-block['width']):
            if (~np.any(world[i:i+block['width'],0])):
                positions.append({'x': i + x_offset,
                                  'y': 0})
                
    for j in range(1,world.shape[1]-block['height']+1):
        for i in range(world.shape[0]-block['width']):
            if ((~np.any(world[i:i+block['width'],j])) & np.any(world[i:i+block['width'],j-1])):
                positions.append({'x': i + x_offset,
                                  'y': j})
    return positions
                
    

def simulate(targets,niter,verbose = False):
    
    block_dims = [{'width':1,
              'height':2},
              {'width':2,
               'height':1},
              {'width':2,
               'height':2},
              {'width':2,
               'height':4},
              {'width':4,
               'height':2}]

    world_bounds = {'left': 5,
                    'right': 13}
    
    columns = ['targetName','run','blockNum','discreteWorld','x','y','w','h']

    df = pd.DataFrame(columns=columns)
    
    for target_name in targets:

        target_map = np.logical_not(np.array(target_maps[target_name]))

        for run in range(0,niter):
            
            discrete_world = np.zeros([18,13]).astype(bool)

            block_num = 0
            completed = False
            tested_all_blocks = False

            while (~completed & ~tested_all_blocks):

                placed = False

                random.shuffle(block_dims)

                b = 0
                while((b < len(block_dims)) & ~placed): #keep trying blocks until placed or none left

                    #select next block from shuffled list
                    block = block_dims[b]
                    if verbose: print(" "*0,'block:', block)

                    # position-centric
                    # enumerate all positions for that block
                    positions = find_positions(discrete_world[5:13,0:8], block, x_offset=5)
                    if verbose: print(positions)

                    random.shuffle(positions) # shuffle positions
                    p = 0

                    while(~placed & (p < len(positions))): #keep trying positions until placed or none left
                        position = positions[p]
                        if verbose: print(" "*4,'position:', position)

                        x_loc = position['x']
                        y_loc = position['y']
                        if verbose: print(" "*4,'selected location x:', x_loc, 'y:', y_loc)

                        # check if valid location
                        # check if in silhouette
                        within_silhouette = check_overlap(x_loc,y_loc,block['width'],block['height'], target_map, mode = 'inside')
                        if verbose: print(" "*4,'within silhouette:', within_silhouette)

                        if within_silhouette:
                             # check if free in current world
                            free_space = check_overlap(x_loc,y_loc,block['width'],block['height'], discrete_world, mode = 'outside')
                            if verbose: print(" "*5,'free space:', free_space)

                            if free_space:

                                # check stability
                                stable = check_stability(x_loc, y_loc, block['width'], block['height'], discrete_world)
                                if verbose: print(" "*4,'stable:', stable)

                                #if added:
                                if stable:
                                    # add to world
                                    discrete_world[x_loc:x_loc+block['width'],y_loc:y_loc+block['height']] = 1
                                    df = df.append({'targetName': target_name,
                                                   'run': run,
                                                   'blockNum': block_num,
                                                   'discreteWorld':discrete_world.copy(),
                                                   'x':x_loc,
                                                   'y':y_loc,
                                                   'w':block['width'],
                                                   'h':block['height']}, ignore_index=True)
                                    if verbose: print(np.rot90(discrete_world.astype(int)))
                                    placed = True
                                    completed = np.all(np.equal(discrete_world,target_map))
                                    block_num += 1
                                else:
                                    p += 1 # check next position
                            else:
                                p += 1 # check next position
                        else:
                            p += 1 # check next position

                    if(p == len(positions)): # if no positions work
                        b += 1 # check next block
                        if verbose: print('incrementing b to ',b)

                if b == len(block_dims):
                    if verbose: print('no viable blocks- giving up')
                    tested_all_blocks = True
                    
                    
    return df

In [219]:
df_random_agent = simulate(targets,105)

In [220]:
df

targetName run blockNum  \
0   hand_selected_004   0        0   
1   hand_selected_004   0        1   
2   hand_selected_004   0        2   
3   hand_selected_004   0        3   
4   hand_selected_004   0        4   
5   hand_selected_004   0        5   
6   hand_selected_004   0        6   
7   hand_selected_004   0        7   
8   hand_selected_004   0        8   
9   hand_selected_005   0        0   
10  hand_selected_005   0        1   
11  hand_selected_005   0        2   
12  hand_selected_005   0        3   
13  hand_selected_005   0        4   
14  hand_selected_005   0        5   
15  hand_selected_005   0        6   
16  hand_selected_005   0        7   
17  hand_selected_005   0        8   
18  hand_selected_005   0        9   
19  hand_selected_005   0       10   

                                        discreteWorld   x  y  w  h  
0   [[False, False, False, False, False, False, Fa...   6  0  1  2  
1   [[False, False, False, False, False, False, Fa...  10  0  2  2  
2   [[False, False, False, False, False, False, Fa...  10  2  2  4  
3   [[False, False, False, False, False, False, Fa...   7  0  2  4  
4   [[False, False, False, False, False, False, Fa...   7  4  2  2  
5   [[False, False, False, False, False, False, Fa...   8  6  4  2  
6   [[False, False, False, False, False, False, Fa...   7  6  1  2  
7   [[False, False, False, False, False, False, Fa...   6  2  1  2  
8   [[False, False, False, False, False, False, Fa...   5  0  1  2  
9   [[False, False, False, False, False, False, Fa...   8  0  2  1  
10  [[False, False, False, False, False, False, Fa...   5  0  1  2  
11  [[False, False, False, False, False, False, Fa...  10  0  2  2  
12  [[False, False, False, False, False, False, Fa...  11  2  1  2  
13  [[False, False, False, False, False, False, Fa...   8  1  2  1  
14  [[False, False, False, False, False, False, Fa...  10  2  1  2  
15  [[False, False, False, False, False, False, Fa...  10  4  1  2  
16  [[False, False, False, False, False, False, Fa...   6  0  1  2  
17  [[False, False, False, False, False, False, Fa...   5  2  4  2  
18  [[False, False, False, False, False, False, Fa...  11  4  1  2  
19  [[False, False, False, False, False, False, Fa...   8  4  1  2

In [223]:
df_random_agent['rawF1DiscreteScore'] = df_random_agent.apply(scoring.get_f1_score_lambda, axis = 1)

In [241]:
df_random_agent

targetName  run blockNum  \
0     hand_selected_004    0        0   
1     hand_selected_004    0        1   
2     hand_selected_004    0        2   
3     hand_selected_004    0        3   
4     hand_selected_004    0        4   
5     hand_selected_004    0        5   
6     hand_selected_004    0        6   
7     hand_selected_004    0        7   
8     hand_selected_004    0        8   
9     hand_selected_004    0        9   
10    hand_selected_004    0       10   
11    hand_selected_004    0       11   
12    hand_selected_004    0       12   
13    hand_selected_004    0       13   
14    hand_selected_004    1        0   
15    hand_selected_004    1        1   
16    hand_selected_004    1        2   
17    hand_selected_004    1        3   
18    hand_selected_004    1        4   
19    hand_selected_004    1        5   
20    hand_selected_004    1        6   
21    hand_selected_004    1        7   
22    hand_selected_004    1        8   
23    hand_selected_004    1        9   
24    hand_selected_004    1       10   
25    hand_selected_004    1       11   
26    hand_selected_004    1       12   
27    hand_selected_004    1       13   
28    hand_selected_004    1       14   
29    hand_selected_004    1       15   
...                 ...  ...      ...   
9780  hand_selected_016  101        3   
9781  hand_selected_016  101        4   
9782  hand_selected_016  101        5   
9783  hand_selected_016  101        6   
9784  hand_selected_016  101        7   
9785  hand_selected_016  101        8   
9786  hand_selected_016  102        0   
9787  hand_selected_016  102        1   
9788  hand_selected_016  102        2   
9789  hand_selected_016  102        3   
9790  hand_selected_016  102        4   
9791  hand_selected_016  102        5   
9792  hand_selected_016  102        6   
9793  hand_selected_016  103        0   
9794  hand_selected_016  103        1   
9795  hand_selected_016  103        2   
9796  hand_selected_016  103        3   
9797  hand_selected_016  103        4   
9798  hand_selected_016  103        5   
9799  hand_selected_016  103        6   
9800  hand_selected_016  104        0   
9801  hand_selected_016  104        1   
9802  hand_selected_016  104        2   
9803  hand_selected_016  104        3   
9804  hand_selected_016  104        4   
9805  hand_selected_016  104        5   
9806  hand_selected_016  104        6   
9807  hand_selected_016  104        7   
9808  hand_selected_016  104        8   
9809  hand_selected_016  104        9   

                                          discreteWorld   x  y  w  h  \
0     [[False, False, False, False, False, False, Fa...  11  0  1  2   
1     [[False, False, False, False, False, False, Fa...   7  0  2  4   
2     [[False, False, False, False, False, False, Fa...   6  0  1  2   
3     [[False, False, False, False, False, False, Fa...   7  4  2  2   
4     [[False, False, False, False, False, False, Fa...  11  2  1  2   
5     [[False, False, False, False, False, False, Fa...   7  6  2  2   
6     [[False, False, False, False, False, False, Fa...   6  2  1  2   
7     [[False, False, False, False, False, False, Fa...   5  0  1  2   
8     [[False, False, False, False, False, False, Fa...  11  4  1  2   
9     [[False, False, False, False, False, False, Fa...  10  0  1  2   
10    [[False, False, False, False, False, False, Fa...  10  2  1  2   
11    [[False, False, False, False, False, False, Fa...  11  6  1  2   
12    [[False, False, False, False, False, False, Fa...  10  4  1  2   
13    [[False, False, False, False, False, False, Fa...  10  6  1  2   
14    [[False, False, False, False, False, False, Fa...  10  0  2  1   
15    [[False, False, False, False, False, False, Fa...   6  0  2  1   
16    [[False, False, False, False, False, False, Fa...  10  1  2  1   
17    [[False, False, False, False, False, False, Fa...   6  1  2  4   
18    [[False, False, False, False, False, False, Fa...  10  2  2  1   
19    [[False, False, False, F

In [248]:
out_path = os.path.join(csv_dir,'block_silhouette_initial_random_agent.csv')
df_random_agent.to_csv(out_path)

In [232]:
import ast

import seaborn as sns
sns.set_context('talk')
sns.set_style('darkgrid')

from IPython.display import clear_output

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)
warnings.filterwarnings("ignore", message="numpy.dtype size changed")
warnings.filterwarnings("ignore", message="numpy.ufunc size changed")

import plotly
import plotly.graph_objects as go
import plotly.io as pio
pio.orca.config.use_xvfb = True
plotly.io.orca.config.save()

import importlib
import trajectory as g

In [246]:
#df_random_agent['discreteWorld']
df_random_agent['discreteWorld'] = df_random_agent['discreteWorld'].apply(lambda a: a*1)

In [247]:
targets = ['hand_selected_004', 'hand_selected_005', 'hand_selected_006',
       'hand_selected_008', 'hand_selected_009', 'hand_selected_011',
       'hand_selected_012', 'hand_selected_016']

df_random_agent['gameID'] = df_random_agent['run']
df_random_agent['phase_extended'] = 'simulation'
df_random_agent['flatDiscreteWorld'] = df_random_agent['discreteWorld'].apply(lambda a: (1+(-1)*np.array(a)).flatten())


importlib.reload(g) ## reimport graph utils
make_plot = True
if make_plot:
    phases = ['simulation']
    for this_target in targets:
        for this_phase in phases:
            g.plot_trajectory_graph(data = df_random_agent, 
                                    target_name = this_target, 
                                    phase = this_phase, 
                                    save = False, 
                                    out_dir = plot_dir,
                                    extension = 'test',
                                    x_lower_bound = 4,
                                    x_upper_bound = 13,
                                    edge_width_scale_factor = 0.4,
                                    node_size_scale_factor = 0.4)

../utils/scoring.py:16: RuntimeWarning:

invalid value encountered in long_scalars

/home/wmccarth/anaconda3/envs/py35/lib/python3.5/site-packages/scipy/ndimage/measurements.py:1359: RuntimeWarning:

invalid value encountered in double_scalars



In [240]:
! git push

Counting objects: 8, done.
Delta compression using up to 16 threads.
Compressing objects: 100% (8/8), done.
Writing objects: 100% (8/8), 1.24 MiB | 5.33 MiB/s, done.
Total 8 (delta 4), reused 0 (delta 0)
remote: Resolving deltas: 100% (4/4), completed with 4 local objects.
To github.com:cogtoolslab/block_construction.git
   179cde0..9442e32  master -> master
